# Get Walgreens locations

#### Load Python tools and Jupyter config

In [1]:
import us 
import json
import black
import requests
import pandas as pd
import jupyter_black
import altair as alt
import geopandas as gpd
from bs4 import BeautifulSoup
from vega_datasets import data
from tqdm.notebook import tqdm, trange

In [2]:
jupyter_black.load()
pd.options.display.max_columns = 100
pd.options.display.max_rows = 1000
pd.options.display.max_colwidth = None
alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

In [3]:
place = "walgreens"
place_formal = "Walgreens"
color = "#a32a33"

---

## Scrape

#### Headers for our request

In [4]:
headers = {
    "authority": "www.walgreens.com",
    "accept": "application/json, text/plain, */*",
    "user-agent": "Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/121.0.0.0 Safari/537.36",
}

#### Import the county's largest ZIP Codes and ensure they have five digits

In [5]:
zips = (
    pd.read_json("../../_reference/data/zip_code_demographics_esri.json")
    .query("population > 5000")
    .sort_values("population", ascending=False)
    .reset_index(drop=True)
)
zips["zipcode"] = zips["zipcode"].astype(str).str.zfill(5)

In [6]:
zips.head()

zipcode      name state_name state  population  population_sqmi  households  \
0   77494      Katy      Texas    TX    163194.0           4061.9     49704.0   
1   77449      Katy      Texas    TX    134540.0           4989.9     38237.0   
2   75070  Mckinney      Texas    TX    123055.0           4960.6     42898.0   
3   11368    Corona   New York    NY    121409.0          58176.7     30724.0   
4   77084   Houston      Texas    TX    121112.0           3000.4     39290.0   

   avg_hh_size  med_hh_income  avg_hh_income  per_cap_income  diversity_index  \
0         3.28       134912.0       172134.0         52497.0             74.9   
1         3.52        78096.0        95889.0         27292.0             84.7   
2         2.87       108330.0       135167.0         47167.0             61.7   
3         3.92        53498.0        73033.0         18735.0             92.8   
4         3.08        76385.0       101532.0         32945.0             85.1   

   area_meters   latitude  longitude  
0  138683779.5  29.744751 -95.826242  
1   92847306.5  29.836113 -95.737685  
2   91997310.5  33.172003 -96.697770  
3    9379884.5  40.749593 -73.855624  
4  139323192.0  29.826236 -95.648321

#### Loop through sample of ZIP Codes to request stores within a 100 miles

In [ ]:
response_list = []

sample = zips.head(5000)

for index, row in tqdm(sample.iterrows(), total=len(sample)):
    params = {
        "requestor": "search",
    }

    json_data = {
        "r": "100",
        "requestType": "dotcom",
        "s": "500",
        "q": f'{row["zipcode"]}',
        "zip": f'{row["zipcode"]}',
    }

    response = requests.post(
        "https://www.walgreens.com/locator/v1/stores/search",
        params=params,
        headers=headers,
        json=json_data,
    )

    # Check if "results" key exists in the response
    if "results" in response.json():
        for r in response.json()["results"]:
            store_number = r["storeNumber"]
            street_address = r["store"]["address"]["street"].title()
            city = r["store"]["address"]["city"].title()
            state = r["store"]["address"]["state"]
            zip_code = r["store"]["address"]["zip"]
            phone = r["store"]["phone"]["number"]
            latitude = r["latitude"]
            longitude = r["longitude"]

            response_dict = {
                "store_number": store_number,
                "street": street_address,
                "city": city,
                "state": state,
                "zip": zip_code,
                "latitude": latitude,
                "longitude": longitude,
            }
            response_list.append(response_dict)
    else:
        print(f"No results for {row['zipcode']}.")

#### Read list of results to a dataframe and remove any duplicates from adjacent ZIP Codes

In [8]:
df = pd.DataFrame(response_list).drop_duplicates(subset="store_number")

#### How many are left? 

In [9]:
len(df)

8446

#### Create a mapping of state abbreviations to full state names using the us library

In [10]:
state_mapping = {state.abbr: state.name for state in us.states.STATES}

#### New column of full state names based on abbreviations

In [11]:
df["state_name"] = df["state"].map(state_mapping)

#### Make sure our brand gets in the dataframe

In [12]:
df["brand"] = place_formal

---

## Geography

#### Make it a geodataframe

In [13]:
df_geo = df.copy()

In [14]:
gdf = gpd.GeoDataFrame(
    df_geo, geometry=gpd.points_from_xy(df_geo.longitude, df_geo.latitude)
)

---

## Maps

#### US states background

In [15]:
background = (
    alt.Chart(alt.topo_feature(data.us_10m.url, feature="states"))
    .mark_geoshape(fill="#e9e9e9", stroke="white")
    .properties(width=800, height=500, title=f"{place_formal} locations")
    .project("albersUsa")
)

#### Location points map

In [16]:
points = (
    alt.Chart(gdf)
    .mark_circle(size=5, color=color)
    .encode(
        longitude="longitude:Q",
        latitude="latitude:Q",
    )
)

point_map = background + points
point_map.configure_view(stroke=None)

alt.LayerChart(...)

#### Location proportional symbols map

In [17]:
symbols = (
    alt.Chart(gdf)
    .transform_aggregate(
        latitude="mean(latitude)",
        longitude="mean(longitude)",
        count="count()",
        groupby=["state"],
    )
    .mark_circle()
    .encode(
        longitude="longitude:Q",
        latitude="latitude:Q",
        size=alt.Size("count:Q", title="Count by state"),
        color=alt.value(color),
        tooltip=["state:N", "count:Q"],
    )
    .properties(
        title=f"Number of {place_formal} in US, by average lon/lat of locations"
    )
)

symbol_map = background + symbols
symbol_map.configure_view(stroke=None)

alt.LayerChart(...)

---

## Exports

#### JSON

In [18]:
df.to_json(
    f"data/processed/{place.lower().replace(' ', '_')}_locations.json",
    indent=4,
    orient="records",
)

#### CSV

In [19]:
df.to_csv(
    f"data/processed/{place.lower().replace(' ', '_')}_locations.csv", index=False
)

#### GeoJSON

In [20]:
gdf.to_file(
    f"data/processed/{place.lower().replace(' ', '_')}_locations.geojson",
    driver="GeoJSON",
)